# Prediction Using Linear Regression
- Set up linear regression model to predict flue NOx levels
- Examine accuracy of model
- Set up models for tcf and f.co and examine accuracy

In [5]:
import pandas as pd
import numpy as np
from jinja2.filters import sync_do_select
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
import plotly.graph_objects as go
import lightgbm as lgb
from sklearn.metrics import mean_absolute_error
from scipy.optimize import minimize, differential_evolution

In [6]:
# read cleaned data
df = pd.read_hdf('../data/clean-data.h5')
df.head()

timestamp  air.flow  air.temp  air.frac  fuel.flow  tc1   tc2  \
0 2020-01-01 00:00:00      2479     28.65      0.24        390   29  1450   
1 2020-01-01 00:01:00      2479     28.65      0.24        390   26  1450   
2 2020-01-01 00:02:00      2479     28.65      0.24        390   26  1446   
3 2020-01-01 00:03:00      2479     28.65      0.24        390   27  1448   
4 2020-01-01 00:04:00      2479     28.65      0.24        390   26  1448   

    tc3   tc4   tcf  ...     f.co2          f.o2     f.ch4     f.nox  \
0  1866  1832  1758  ...  0.031799  2.784636e-13  0.003849  0.000788   
1  1863  1835  1760  ...  0.032406  2.678304e-13  0.003662  0.000790   
2  1867  1833  1760  ...  0.031569  2.608832e-13  0.003831  0.000793   
3  1862  1837  1760  ...  0.032599  2.557492e-13  0.003604  0.000792   
4  1867  1836  1755  ...  0.031396  2.694801e-13  0.003752  0.000799   

       f.co  spec stoppage hub  shift trial  
0  0.000289   CIA    False  22      B   1.0  
1  0.000314   CIA    False  22      B   1.0  
2  0.000308   CIA    False  22      B   1.0  
3  0.000306   CIA    False  22      B   1.0  
4  0.000300   CIA    False  22      B   1.0  

[5 rows x 21 columns]

In [7]:
# list of input features
inputs = ['air.flow', 'air.temp', 'air.frac', 'fuel.flow']

# list of output features
columns = ['tc1', 'tc2', 'tc3', 'tc4', 'tcf', 'f.h2o', 'f.co2', 'f.o2', 'f.ch4', 'f.co', 'f.nox']

# selected output feature
output = ['f.nox']

In [8]:
# split the data into training (80%) and testing (20%) sets
X_train, X_test, y_train, y_test = train_test_split(df[inputs], df[output], test_size=0.2, random_state=42)

# initiate the linear regression model
model = LinearRegression()

# fit the linear model using the input data
model.fit(X_train, y_train)

LinearRegression()

In [9]:
# determine r2 score for model
score = model.score(X_test, y_test)
display('R2: ' + str(score))

# predict output for test data
predictions = model.predict(X_test)

# create dataframe with prediction results
predictionsDF = pd.DataFrame(predictions, columns=output)
predictionsDF.head()

'R2: 0.0993494275561162'

f.nox
0  0.006905
1  0.011851
2  0.004817
3  0.012578
4  0.004817

In [10]:
# Plot parity of actual versus predicted values
parity = go.Figure()

# add test v. predicted markers
parity.add_trace(
    go.Scatter(
        x=y_test['f.nox'],
        y=predictionsDF['f.nox'],
        mode='markers',
        name='results'
    )
)

# add parity line
parity.add_trace(
    go.Scatter(
        x=y_test['f.nox'],
        y=y_test['f.nox'],
        name='parity'
    )
)

# update layout and title
parity.update_layout(height=800, width=800, title="NOx Actual vs. Predicted")
parity.update_xaxes(title='Actual NOx')
parity.update_yaxes(title='Predicted NOx')
#display figure
parity.show()

In [11]:
# Build linear regression model for flue temperature (tcf)
# Use same train/test split as before
output_tcf = ['tcf']

# split the data into training (80%) and testing (20%) sets
X_train_tcf, X_test_tcf, y_train_tcf, y_test_tcf = train_test_split(
    df[inputs],
    df[output_tcf],
    test_size=0.2,
    random_state=42
)

# initiate the linear regression model
model_tcf = LinearRegression()

# fit the linear model using the input data
model_tcf.fit(X_train_tcf, y_train_tcf)

# determine r2 score for model
score_tcf = model_tcf.score(X_test_tcf, y_test_tcf)
display('R2 for TCF: ' + str(score_tcf))

# predict output for test data
predictions_tcf = model_tcf.predict(X_test_tcf)
predictionsDF_tcf = pd.DataFrame(predictions_tcf, columns=output_tcf)

# Plot parity of actual versus predicted values for flue temperature
parity_tcf = go.Figure()

# add test v. predicted markers
parity_tcf.add_trace(
    go.Scatter(
        x=y_test_tcf['tcf'],
        y=predictionsDF_tcf['tcf'],
        mode='markers',
        name='results'
    )
)

# add parity line
parity_tcf.add_trace(
    go.Scatter(
        x=y_test_tcf['tcf'],
        y=y_test_tcf['tcf'],
        name='parity'
    )
)

# update layout and title
parity_tcf.update_layout(height=800, width=800, title="Flue Temperature Actual vs. Predicted")
parity_tcf.update_xaxes(title='Actual TCF (°C)')
parity_tcf.update_yaxes(title='Predicted TCF (°C)')

# display figure
parity_tcf.show()

'R2 for TCF: 0.7611991641990963'

In [12]:
# Build linear regression model for CO2 emissions (f.co2)
output_co2 = ['f.co2']

# split the data into training (80%) and testing (20%) sets
X_train_co2, X_test_co2, y_train_co2, y_test_co2 = train_test_split(
    df[inputs],
    df[output_co2],
    test_size=0.2,
    random_state=42
)

# initiate the linear regression model
model_co2 = LinearRegression()

# fit the linear model using the input data
model_co2.fit(X_train_co2, y_train_co2)

# determine r2 score for model
score_co2 = model_co2.score(X_test_co2, y_test_co2)
display('R2 for CO2: ' + str(score_co2))

# predict output for test data
predictions_co2 = model_co2.predict(X_test_co2)
predictionsDF_co2 = pd.DataFrame(predictions_co2, columns=output_co2)

# Plot parity of actual versus predicted values for CO2 emissions
parity_co2 = go.Figure()

# add test v. predicted markers
parity_co2.add_trace(
    go.Scatter(
        x=y_test_co2['f.co2'],
        y=predictionsDF_co2['f.co2'],
        mode='markers',
        name='results'
    )
)

# add parity line
parity_co2.add_trace(
    go.Scatter(
        x=y_test_co2['f.co2'],
        y=y_test_co2['f.co2'],
        name='parity'
    )
)

# update layout and title
parity_co2.update_layout(height=800, width=800, title="CO2 Emissions Actual vs. Predicted")
parity_co2.update_xaxes(title='Actual CO2 (tonne/hr)')
parity_co2.update_yaxes(title='Predicted CO2 (tonne/hr)')

# display figure
parity_co2.show()

'R2 for CO2: 0.7714021644644824'

In [13]:
# Build LightGBM model for NOx emissions
# Use the same train/test split as linear regression
# (already have X_train, X_test, y_train, y_test for NOx)

# Create LightGBM regressor
model_lgb_nox = lgb.LGBMRegressor(
    n_estimators=100,
    learning_rate=0.1,
    random_state=42
)

# Fit the model using the training data
model_lgb_nox.fit(X_train, y_train)

# Predict on test data
predictions_lgb_nox = model_lgb_nox.predict(X_test)

# Create dataframe with predictions
predictionsDF_lgb_nox = pd.DataFrame(predictions_lgb_nox, columns=output)

# Calculate R² score
score_lgb_nox = model_lgb_nox.score(X_test, y_test)
display('LightGBM R2 for NOx: ' + str(score_lgb_nox))

# Plot parity of actual versus predicted values for LightGBM NOx model
parity_lgb_nox = go.Figure()

# add test v. predicted markers
parity_lgb_nox.add_trace(
    go.Scatter(
        x=y_test['f.nox'],
        y=predictionsDF_lgb_nox['f.nox'],
        mode='markers',
        name='results'
    )
)

# add parity line
parity_lgb_nox.add_trace(
    go.Scatter(
        x=y_test['f.nox'],
        y=y_test['f.nox'],
        name='parity'
    )
)

# update layout and title
parity_lgb_nox.update_layout(height=800, width=800, title="LightGBM NOx Actual vs. Predicted")
parity_lgb_nox.update_xaxes(title='Actual NOx')
parity_lgb_nox.update_yaxes(title='Predicted NOx')

# display figure
parity_lgb_nox.show()

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000461 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 191
[LightGBM] [Info] Number of data points in the train set: 105359, number of used features: 4
[LightGBM] [Info] Start training from score 0.007984


'LightGBM R2 for NOx: 0.9999476812166448'

In [14]:
# Build LightGBM model for flue temperature
# Use the same train/test split as linear regression for tcf

# Create LightGBM regressor
model_lgb_tcf = lgb.LGBMRegressor(
    n_estimators=100,
    learning_rate=0.1,
    random_state=42
)

# Fit the model using the training data
model_lgb_tcf.fit(X_train_tcf, y_train_tcf)

# Predict on test data
predictions_lgb_tcf = model_lgb_tcf.predict(X_test_tcf)

# Create dataframe with predictions
predictionsDF_lgb_tcf = pd.DataFrame(predictions_lgb_tcf, columns=output_tcf)

# Calculate R² score
score_lgb_tcf = model_lgb_tcf.score(X_test_tcf, y_test_tcf)
display('LightGBM R2 for TCF: ' + str(score_lgb_tcf))

# Plot parity of actual versus predicted values for LightGBM TCF model
parity_lgb_tcf = go.Figure()

# add test v. predicted markers
parity_lgb_tcf.add_trace(
    go.Scatter(
        x=y_test_tcf['tcf'],
        y=predictionsDF_lgb_tcf['tcf'],
        mode='markers',
        name='results'
    )
)

# add parity line
parity_lgb_tcf.add_trace(
    go.Scatter(
        x=y_test_tcf['tcf'],
        y=y_test_tcf['tcf'],
        name='parity'
    )
)

# update layout and title
parity_lgb_tcf.update_layout(height=800, width=800, title="LightGBM Flue Temperature Actual vs. Predicted")
parity_lgb_tcf.update_xaxes(title='Actual TCF (°C)')
parity_lgb_tcf.update_yaxes(title='Predicted TCF (°C)')

# display figure
parity_lgb_tcf.show()

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000446 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 191
[LightGBM] [Info] Number of data points in the train set: 105359, number of used features: 4
[LightGBM] [Info] Start training from score 1670.509392


'LightGBM R2 for TCF: 0.9999863375702582'

In [15]:
 # Build LightGBM model for CO2 emissions
# Use the same train/test split as linear regression for CO2

# Create LightGBM regressor
model_lgb_co2 = lgb.LGBMRegressor(
    n_estimators=100,
    learning_rate=0.1,
    random_state=42
)

# Fit the model using the training data
model_lgb_co2.fit(X_train_co2, y_train_co2)

# Predict on test data
predictions_lgb_co2 = model_lgb_co2.predict(X_test_co2)

# Create dataframe with predictions
predictionsDF_lgb_co2 = pd.DataFrame(predictions_lgb_co2, columns=output_co2)

# Calculate R² score
score_lgb_co2 = model_lgb_co2.score(X_test_co2, y_test_co2)
display('LightGBM R2 for CO2: ' + str(score_lgb_co2))

# Plot parity of actual versus predicted values for LightGBM CO2 model
parity_lgb_co2 = go.Figure()

# add test v. predicted markers
parity_lgb_co2.add_trace(
    go.Scatter(
        x=y_test_co2['f.co2'],
        y=predictionsDF_lgb_co2['f.co2'],
        mode='markers',
        name='results'
    )
)

# add parity line
parity_lgb_co2.add_trace(
    go.Scatter(
        x=y_test_co2['f.co2'],
        y=y_test_co2['f.co2'],
        name='parity'
    )
)

# update layout and title
parity_lgb_co2.update_layout(height=800, width=800, title="LightGBM CO2 Emissions Actual vs. Predicted")
parity_lgb_co2.update_xaxes(title='Actual CO2 (tonne/hr)')
parity_lgb_co2.update_yaxes(title='Predicted CO2 (tonne/hr)')

# display figure
parity_lgb_co2.show()

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000368 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 191
[LightGBM] [Info] Number of data points in the train set: 105359, number of used features: 4
[LightGBM] [Info] Start training from score 0.041626


'LightGBM R2 for CO2: 0.9833328919378389'

In [16]:
# Linear Regression MAE for NOx
mae_linear_nox = mean_absolute_error(y_test['f.nox'], predictionsDF['f.nox'])
display('Linear Regression MAE for NOx: ' + str(mae_linear_nox))

# LightGBM MAE for NOx
mae_lgb_nox = mean_absolute_error(y_test['f.nox'], predictionsDF_lgb_nox['f.nox'])
display('LightGBM MAE for NOx: ' + str(mae_lgb_nox))

# Comparison
display('NOx MAE Improvement: ' + str((mae_linear_nox - mae_lgb_nox) / mae_linear_nox * 100) + '%')

# Linear Regression MAE for TCF
mae_linear_tcf = mean_absolute_error(y_test_tcf['tcf'], predictionsDF_tcf['tcf'])
display('Linear Regression MAE for TCF: ' + str(mae_linear_tcf))

# LightGBM MAE for TCF
mae_lgb_tcf = mean_absolute_error(y_test_tcf['tcf'], predictionsDF_lgb_tcf['tcf'])
display('LightGBM MAE for TCF: ' + str(mae_lgb_tcf))

# Comparison
display('TCF MAE Improvement: ' + str((mae_linear_tcf - mae_lgb_tcf) / mae_linear_tcf * 100) + '%')

# Linear Regression MAE for CO2
mae_linear_co2 = mean_absolute_error(y_test_co2['f.co2'], predictionsDF_co2['f.co2'])
display('Linear Regression MAE for CO2: ' + str(mae_linear_co2))

# LightGBM MAE for CO2
mae_lgb_co2 = mean_absolute_error(y_test_co2['f.co2'], predictionsDF_lgb_co2['f.co2'])
display('LightGBM MAE for CO2: ' + str(mae_lgb_co2))

# Comparison
display('CO2 MAE Improvement: ' + str((mae_linear_co2 - mae_lgb_co2) / mae_linear_co2 * 100) + '%')

'Linear Regression MAE for NOx: 0.008213651320126048'

'LightGBM MAE for NOx: 4.059477595657994e-05'

'NOx MAE Improvement: 99.50576455738862%'

'Linear Regression MAE for TCF: 150.15417403922802'

'LightGBM MAE for TCF: 1.4928804860367397'

'TCF MAE Improvement: 99.00576824081712%'

'Linear Regression MAE for CO2: 0.0030279606345131075'

'LightGBM MAE for CO2: 0.0010353649994085008'

'CO2 MAE Improvement: 65.80652378345776%'

In [17]:
# Generic objective function
def minimize_emission(params, model):
    X = pd.DataFrame([params], columns=['air.flow', 'air.temp', 'air.frac', 'fuel.flow'])
    return model.predict(X)[0]


# Bounds: [air.flow, air.temp, air.frac, fuel.flow]
bounds = [(1500, 10000), (20, 200), (0.21, 1.0), (282, 282)]

# 1. Optimize for minimum NOx
result_nox = differential_evolution(
    lambda x: minimize_emission(x, model_lgb_nox),
    bounds=bounds,
    seed=42
)

print("Optimal NOx Configuration:")
print(f"Air Flow: {result_nox.x[0]:.2f}, Air Temp: {result_nox.x[1]:.2f}, O2 Frac: {result_nox.x[2]:.4f}, Fuel Flow: {result_nox.x[3]:.4f}")
print(f"Minimum NOx: {result_nox.fun:.6f}\n")

# 2. Optimize for minimum CO2
result_co2 = differential_evolution(
    lambda x: minimize_emission(x, model_lgb_co2),
    bounds=bounds,
    seed=42
)

print("Optimal CO2 Configuration:")
print(f"Air Flow: {result_co2.x[0]:.2f}, Air Temp: {result_co2.x[1]:.2f}, O2 Frac: {result_co2.x[2]:.4f}, Fuel Flow: {result_co2.x[3]:.4f}")
print(f"Minimum CO2: {result_co2.fun:.6f}")

Optimal NOx Configuration:
Air Flow: 7701.54, Air Temp: 23.08, O2 Frac: 0.9994, Fuel Flow: 282.0000
Minimum NOx: 0.000696

Optimal CO2 Configuration:
Air Flow: 2834.67, Air Temp: 107.49, O2 Frac: 0.2142, Fuel Flow: 282.0000
Minimum CO2: 0.025462
